In [2]:
import os
import librosa
import tensorflow as tf
import numpy as np
from tensorflow.image import resize

In [3]:
#loading model
model = tf.keras.models.load_model("./Trained_model.keras")

In [4]:
classes = [ 'blues','classical','country','disco','hiphop','jazz','metal','pop','reggae','rock']

# Single audio Preprocessing

In [5]:
#loading and preprocessing audio file
def load_and_preprocess_file(file_path,target_shape=(150,150)):
    data = []
    audio_data,sample_rate = librosa.load(file_path,sr=None)
    chunk_duration=4
    overlap_duration=2
    #convert duration to sample
    chunk_samples = chunk_duration * sample_rate
    overlap_samples = overlap_duration * sample_rate
                
    #calculate the number of chunks
    num_chunks = int(np.ceil((len(audio_data)-chunk_samples)/(chunk_samples-overlap_samples)))+1
    #iterate 
    for i in range (num_chunks):
        start = i*(chunk_samples-overlap_samples)
        end = start+chunk_samples
        chunk = audio_data[start:end]
        spectrogram = librosa.feature.melspectrogram(y=chunk, sr=sample_rate)
                
        #Resize matrix based on target shape
        spectrogram = resize(np.expand_dims(spectrogram,axis=-1),target_shape)
        data.append(spectrogram)

    return np.array(data)



# Playing a sound

In [88]:
from IPython.display import Audio
file_path = "./test_music/mary_christmus_classical(chosic.com).mp3"
y, sr = librosa.load(file_path, sr=44100)
Audio(data=y, rate=sr)

In [89]:
file_path = "./test_music/mary_christmus_classical(chosic.com).mp3"
X_test = load_and_preprocess_file(file_path)

In [90]:
X_test.shape

(26, 150, 150, 1)

# Model Prediction

In [91]:
def model_prediction(X_test):
    y_pred = model.predict(X_test)
    predicted_categories = np.argmax(y_pred,axis=1)
    unique_elements,counts = np.unique(predicted_categories,return_counts=True)
    max_count = np.max(counts)
    max_elements = unique_elements[counts == max_count]
    return  max_elements[0]

In [92]:
c_index = model_prediction(X_test)

1/1 [==============================] - 0s 221ms/step


In [93]:
c_index

1

In [94]:
print("Model Prediction: Model_prediction ---: ", classes[c_index])

Model Prediction: Model_prediction ---:  classical
